In [1]:
alpha = 0.65
f(k) = k.^alpha
u(x) = log(x)
beta = 0.95

#grid for state variable k and action variable s:
grid_max = 2
grid_size = 500
grid = linspace(1e-6, grid_max, grid_size)

linspace(1.0e-6,2.0,500)

In [2]:
C = reshape(f(grid),grid_size,1).-reshape(grid,1,grid_size)
coord = repmat(collect(1:grid_size),1,grid_size) #coordinate matrix 
s_indices = coord[C.>0]
a_indices = transpose(coord)[C.>0]
L = length(a_indices)


118841

In [3]:
R = u(C[C.>0]);

In [4]:
Q = spzeros(L,grid_size)

for i in 1:L
  Q[i,a_indices[i]] = 1
end

In [5]:
using QuantEcon
using Benchmarks
using ProfileView

In [6]:
@time ddp = DiscreteDP(R, Q, beta, s_indices, a_indices);
#@profile ddp = DiscreteDP(R, Q, beta, s_indices, a_indices);
#ProfileView.view()

  1.184941 seconds (578.47 k allocations: 491.487 MB, 2.83% gc time)


QuantEcon.DiscreteDP{Float64,2,1,Float64,Int64}([-8.98806,-3.58752,-3.74402,-3.92964,-4.15775,-4.45376,-4.8761,-5.62164,-3.13704,-3.23392  …  -3.26739,-3.37852,-3.50357,-3.64652,-3.81336,-4.01374,-4.26458,-4.60021,-5.10907,-6.19789],118841x500 Array{Float64,2}:
 1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  …  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  …  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  1.0  0.0  0.0  0.0  0.0  0.0  

DiscreteDP allocates about 480 MB permanently!
Because of "full(Q)" call in constructor! TODO: use sparse matrix throughout ddp!
grid_size=1500 yields 12 GB allocations, but not in the memory. Where is it then stored?! "Virtual Memory" increases by 12 GB in size!

In [7]:
@profile results = solve(ddp, PFI);
ProfileView.view()

400 MB permanently!

In [ ]:
results.mc

In [ ]:
v, sigma, num_iter = results.v, results.sigma, results.num_iter

num_iter

In [ ]:
c = f(grid) - grid[sigma]

ab = alpha * beta
c1 = (log(1 - alpha * beta) + log(alpha * beta) * alpha * beta / (1 - alpha * beta)) / (1 - beta)
c2 = alpha / (1 - alpha * beta)

v_star(k) = c1 + c2 * log(k)
c_star(k) = (1 - alpha * beta) * k.^alpha

using PyPlot
fig, (ax1, ax2) = subplots(1, 2, figsize=(14, 4))


ax1[:set_ylim](-40, -32)
ax1[:set_xlim](grid[1], grid[end])
ax2[:set_xlim](grid[1], grid[end])

lb0 = "discrete value function"
ax1[:plot](grid, v, lw=2, alpha=0.6, label=lb0)
lb0 = "continuous value function"
ax1[:plot](grid, v_star(grid), "k-", lw=1.5, alpha=0.8, label=lb0)
ax1[:legend](loc="upper left")

lb1 = "discrete optimal consumption"
ax2[:plot](grid, c, "b-", lw=2, alpha=0.6, label=lb1)
lb1 = "continuous optimal consumption"
ax2[:plot](grid, c_star(grid), "k-", lw=1.5, alpha=0.8, label=lb1)
ax2[:legend](loc="upper left")

maximum(abs(v - v_star(grid)))

maximum(abs(v - v_star(grid))[2:end])

maximum(abs(c - c_star(grid)))

In [ ]:
maximum(abs(v - v_star(grid)))

In [ ]:
maximum(abs(v - v_star(grid))[2:end])

In [ ]:
maximum(abs(c - c_star(grid)))

In [ ]:
cdiff = diff(c)
all(cdiff.>=0)

In [ ]:
dec_ind = collect(1:length(c)-1)[(cdiff.<0)];

In [ ]:
length(dec_ind)

In [ ]:
maximum(abs(cdiff[dec_ind]))

In [ ]:
all(diff(v).>=0)

Comparison of the solution methods
--

In [ ]:
@time res1 = solve(ddp, VFI, max_iter=500, epsilon=1e-4);

In [ ]:
res1.num_iter

In [ ]:
sigma==res1.sigma

In [ ]:
@time res2 = solve(ddp, MPFI, max_iter=500, epsilon=1e-4);

In [ ]:
res2.num_iter

In [ ]:
sigma==res2.sigma

Replication of the figures
--

In [ ]:
w = 5 * log(grid) - 25  # Initial condition
n = 35
fig, ax = subplots(figsize=(8,5))
ax[:set_ylim](-40, -20)
ax[:set_xlim](minimum(grid), maximum(grid))
lb = "initial condition"
jet = ColorMap("jet")[:__call__]
ax[:plot](grid, w, color=jet(0), lw=2, alpha=0.6, label=lb)
for i in 0:n-1
    w = bellman_operator(ddp, w)
    ax[:plot](grid, w, color=jet(i / n), lw=2, alpha=0.6)
end
lb = "true value function"
ax[:plot](grid, v_star(grid), "k-", lw=2, alpha=0.8, label=lb)
ax[:legend](loc="upper left")

In [ ]:
bellman(w) = bellman_operator(ddp,w)

fig, ax = subplots(3, 1, figsize=(8, 10))
true_c = c_star(grid)

for (i, n) in enumerate([2, 4, 6])
    w = 5 * u(grid) - 25  # Initial condition
    
    ax[i][:set_ylim](0, 1)
    ax[i][:set_xlim](0, 2)
    ax[i][:set_yticks]((0, 1))
    ax[i][:set_xticks]((0, 2))

    w = compute_fixed_point(bellman, w, max_iter=n, print_skip=1)
    sigma = compute_greedy(ddp,w)
    c_policy = f(grid) - grid[sigma]
    
    ax[i][:plot](grid, c_policy, "b-", lw=2, alpha=0.8,
               label="approximate optimal consumption policy")
    ax[i][:plot](grid, true_c, "k-", lw=2, alpha=0.8,
               label="true optimal consumption policy")
    ax[i][:legend](loc="upper left")
    ax[i][:set_title]("$n value function iterations")
end